In [3]:
import numpy as np
import sys
import os
import numpy as np
import matplotlib.pyplot as plt
from importlib import reload
import nibabel as nib
import pandas as pd
from IPython.display import clear_output
import importlib
from skimage import morphology
from skimage.segmentation import find_boundaries
import porespy as ps
from skimage.morphology import disk, binary_dilation
from mpl_toolkits import mplot3d
import math
import ast

In [2]:
especimens = [
    "20190504_E1",
    "20190404_E2",
    "20190520_E4",
    "20190516_E3",
    "20190806_E3",
    "20190520_E2",
    "20190401_E3",
    "20190517_E1",
    "20190520_E1",
    '20190401_E1',
]

In [12]:
ESPECIMEN = "20190401_E2"

In [13]:
FILE_DF = f"/Users/dvarelat/Documents/MASTER/TFM/DATA/EXTRACTION/{ESPECIMEN}/cell_properties.csv"
gasp_mem = f"/Users/dvarelat/Documents/MASTER/TFM/DATA/RESULTS/membranes/GASP_PNAS/{ESPECIMEN}_mGFP_CardiacRegion_0.5_XYZ_predictions_GASP.nii.gz"

In [14]:
df_clean = pd.read_csv(FILE_DF)
print(df_clean.shape)
pred_mem = nib.load(gasp_mem).get_fdata()
print(pred_mem.shape)

(6437, 8)
(881, 900, 480)


In [15]:
img_mem = morphology.label(pred_mem)
props_mem = ps.metrics.regionprops_3D(img_mem)

### ADD EIGENVALUES AND VECTORS

In [7]:
def eccentricity_3d(eigenvalues):
    l1, l2, l3 = eigenvalues
    if l1 == 0:
        return 0
    return math.sqrt(1 - l2 / l1)

In [17]:
dict_label_cell = dict(zip(df_clean.original_labels, df_clean.cell_in_props))
values = []
vectors = []
for i, cell_id in enumerate(list(df_clean.original_labels)):
    prop = props_mem[dict_label_cell[cell_id]]
    T = prop.inertia_tensor
    eigvals, evecs = np.linalg.eig(T)
    idx = eigvals.argsort()[::-1]   
    eigenValues = eigvals[idx]
    eigenVectors = evecs[:,idx]
    values.append(np.around(eigenValues, 3).tolist())
    vectors.append(np.around(eigenVectors, 3).T.tolist())

In [19]:
df_clean["eigenvalues"] = values
df_clean["eigenvectors"] = vectors
df_clean["eccentricity3d"] = df_clean["eigenvalues"].apply(lambda x: round(eccentricity_3d(x),3))

In [20]:
df_clean.to_csv(FILE_DF, index=False, header=True)

# LOOP

In [8]:
for ESPECIMEN in especimens:
    print(ESPECIMEN)
    FILE_DF = f"/Users/dvarelat/Documents/MASTER/TFM/DATA/EXTRACTION/{ESPECIMEN}/cell_properties.csv"
    gasp_mem = f"/Users/dvarelat/Documents/MASTER/TFM/DATA/RESULTS/membranes/GASP_PNAS/{ESPECIMEN}_mGFP_XYZ_predictions_GASP.nii.gz"
    df_clean = pd.read_csv(FILE_DF)
    print(df_clean.shape)
    pred_mem = nib.load(gasp_mem).get_fdata()
    print(pred_mem.shape)
    img_mem = morphology.label(pred_mem)
    props_mem = ps.metrics.regionprops_3D(img_mem)
    dict_label_cell = dict(zip(df_clean.original_labels, df_clean.cell_in_props))
    values = []
    vectors = []
    for i, cell_id in enumerate(list(df_clean.original_labels)):
        prop = props_mem[dict_label_cell[cell_id]]
        T = prop.inertia_tensor
        eigvals, evecs = np.linalg.eig(T)
        idx = eigvals.argsort()[::-1]   
        eigenValues = eigvals[idx]
        eigenVectors = evecs[:,idx]
        values.append(np.around(eigenValues, 3).tolist())
        vectors.append(np.around(eigenVectors, 3).T.tolist())
    df_clean["eigenvalues"] = values
    df_clean["eigenvectors"] = vectors
    df_clean["eccentricity3d"] = df_clean["eigenvalues"].apply(lambda x: round(eccentricity_3d(x),3))
    df_clean.to_csv(FILE_DF, index=False, header=True)
    print("--------------")

20190504_E1
(2637, 10)
(1024, 1024, 413)
--------------
20190404_E2
(7826, 10)
(1024, 1024, 448)
--------------
20190520_E4
(1532, 10)
(1024, 1024, 220)
--------------
20190516_E3
(7865, 10)
(1024, 1024, 594)
--------------
20190806_E3
(5216, 10)
(1024, 1024, 541)
--------------
20190520_E2
(3299, 10)
(1024, 1024, 493)
--------------
20190401_E3
(5127, 10)
(1024, 1024, 403)
--------------
20190517_E1
(7601, 10)
(1024, 1024, 563)
--------------
20190520_E1
(7739, 10)
(1024, 1024, 443)
--------------
20190401_E1
(4811, 10)
(1024, 1024, 680)
--------------


In [9]:
for ESPECIMEN in especimens:
    print(ESPECIMEN)
    FILE_DF = f"/Users/dvarelat/Documents/MASTER/TFM/DATA/EXTRACTION/{ESPECIMEN}/cell_properties.csv"
    gasp_mem = f"/Users/dvarelat/Documents/MASTER/TFM/DATA/RESULTS/membranes/GASP_PNAS/{ESPECIMEN}_mGFP_XYZ_predictions_GASP.nii.gz"
    df_clean = pd.read_csv(FILE_DF)
    print(df_clean.shape)
    pred_mem = nib.load(gasp_mem).get_fdata()
    print(pred_mem.shape)
    img_mem = morphology.label(pred_mem)
    props_mem = ps.metrics.regionprops_3D(img_mem)
    solidities = []
    feret = []
    for i in df_clean.cell_in_props:
        solidities.append(props_mem[i].solidity)
        feret.append(props_mem[i].feret_diameter_max)
    df_clean["solidity"] = solidities
    df_clean["feret_diameter_max"] = feret
    print("--------------")

20190504_E1
(2637, 13)
(1024, 1024, 413)
--------------
20190404_E2
(7826, 13)
(1024, 1024, 448)
--------------
20190520_E4
(1532, 13)
(1024, 1024, 220)
--------------
20190516_E3
(7865, 13)
(1024, 1024, 594)
--------------
20190806_E3
(5216, 13)
(1024, 1024, 541)
--------------
20190520_E2
(3299, 13)
(1024, 1024, 493)
--------------
20190401_E3
(5127, 13)
(1024, 1024, 403)
--------------
20190517_E1
(7601, 13)
(1024, 1024, 563)
--------------
20190520_E1
(7739, 13)
(1024, 1024, 443)
--------------
20190401_E1
(4811, 13)
(1024, 1024, 680)
--------------


### PROPIEDAD ACROSS CELLS

### ordenar por el centroide 

In [52]:
df

cell_in_props  volumes  sphericities  original_labels        centroids  \
3146           4404      802      0.636140             94.0    [545, 127, 1]   
3044           4254     1020      0.794195             87.0    [506, 140, 1]   
3918           5527      801      0.972556            105.0    [677, 108, 1]   
2129           3079     1184      0.758886             62.0    [297, 144, 2]   
3843           5408     2068      0.905316            103.0     [673, 80, 2]   
...             ...      ...           ...              ...              ...   
4076           5756      806      1.025263           7171.0  [700, 746, 390]   
4767           6665     1739      0.842504           7170.0  [802, 700, 390]   
3366           4714      645      0.813826           7177.0  [582, 467, 391]   
3488           4890     1297      0.702234           7176.0  [602, 532, 391]   
4887           6817     1123      0.710152           7179.0  [821, 693, 391]   

      lines  axis_major_length  axis_minor_length         volumeRGB  \
3146    0.0          30.943105           4.307028  [0, 3, 252, 255]   
3044    0.0          23.422889           5.053191  [0, 4, 251, 255]   
3918    0.0          20.057629           5.585059  [0, 3, 252, 255]   
2129    0.0          29.355426           6.109003  [0, 5, 250, 255]   
3843    0.0          26.805818           7.375232  [0, 8, 247, 255]   
...     ...                ...                ...               ...   
4076    0.0          14.933383           9.589662  [0, 3, 252, 255]   
4767    0.0          20.905029          11.048483  [0, 7, 248, 255]   
3366    0.0          17.028353           6.338456  [0, 3, 252, 255]   
3488    0.0          26.160637           7.089788  [0, 5, 250, 255]   
4887    0.0          32.115748           6.744796  [0, 4, 251, 255]   

           sphericityRGB  nuclei_label_cent  nuclei_cell_in_props  \
3146  [0, 105, 150, 255]               -1.0                    -1   
3044   [0, 164, 91, 255]              241.0                  6069   
3918   [0, 229, 26, 255]              333.0                  8572   
2129  [0, 151, 104, 255]              155.0                  4242   
3843   [0, 205, 50, 255]              332.0                  8483   
...                  ...                ...                   ...   
4076    [0, 249, 6, 255]            23793.0                  8992   
4767   [0, 181, 74, 255]            23734.0                 10780   
3366   [0, 171, 84, 255]               -1.0                    -1   
3488  [0, 130, 125, 255]            23247.0                  7422   
4887  [0, 133, 122, 255]            23347.0                 11019   

                   eigenvalues  \
3146  [57.224, 48.801, 10.277]   
3044  [44.572, 28.708, 18.417]   
3918  [31.773, 21.675, 13.217]   
2129  [52.988, 44.953, 11.767]   
3843   [64.91, 38.647, 31.703]   
...                        ...   
4076  [20.629, 15.748, 14.077]   
4767  [35.876, 27.954, 20.129]   
3366  [22.814, 16.507, 10.325]   
3488  [48.419, 36.732, 16.713]   
4887  [59.356, 53.846, 10.059]   

                                           eigenvectors  eccentricity3d  \
3146  [[0.03, 0.065, 0.997], [0.362, 0.93, -0.072], ...           0.384   
3044  [[-0.025, -0.045, 0.999], [0.637, 0.769, 0.05]...           0.597   
3918  [[-0.034, -0.041, 0.999], [0.954, 0.298, 0.045...           0.564   
2129  [[0.008, 0.043, 0.999], [-0.205, 0.978, -0.041...           0.389   
3843  [[-0.054, -0.002, 0.999], [0.687, 0.725, 0.039...           0.636   
...                                                 ...             ...   
4076  [[0.133, 0.427, 0.894], [0.977, -0.211, -0.044...           0.486   
4767  [[0.008, 0.222, 0.975], [0.956, 0.284, -0.073]...           0.470   
3366  [[-0.019, 0.087, -0.996], [-0.019, 0.996, 0.08...           0.526   
3488  [[-0.032, 0.105, 0.994], [0.995, 0.101, 0.022]...           0.491   
4887  [[0.047, 0.013, 0.999], [0.909, 0.415, -0.048]...           0.305   

        especimen name_lines  centroids_z  
3146  201

In [20]:
fig = px.scatter(df , x="cell_in_props", y="eccentricity3d", color="name_lines")
fig.show()

In [32]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler


In [33]:
pca = PCA(n_components=3)

In [34]:
dfall.name_lines.unique()

array(['back', 'proximal', 'somatic', 'splanchnic', 'myocardium',
       'kdo_myo'], dtype=object)

In [44]:
dfsubset = dfall[dfall.name_lines.isin(["myocardium", "splanchnic", "somatic"])]
specimen = dfsubset.especimen.values
target = dfsubset.name_lines.values
dfsubset = dfsubset[["volumes", "sphericities", "axis_major_length", "axis_minor_length", "eccentricity3d"]]

In [45]:
x = dfsubset.values
x = StandardScaler().fit_transform(x)

In [46]:
principalComponents = pca.fit_transform(x)
principalDf = pd.DataFrame(data = principalComponents, columns = ['pc1', 'pc2', 'pc3'])
principalDf.shape

(33274, 3)

In [47]:
pca.explained_variance_ratio_


array([0.48172479, 0.24827062, 0.19797656])

In [48]:
principalDf["target"] = target
principalDf["specimen"] = specimen

In [50]:
fig = px.scatter(principalDf[principalDf["specimen"]  == "20190401_E3"] , x="pc1", y="pc2", color="target")
fig.show()

In [51]:
fig = px.scatter_3d(principalDf[principalDf["specimen"]  == "20190401_E3"], x='pc1', y='pc2', z='pc3',
                    color='target')
fig.show()